In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import copy
import yaml
import datetime
from typing import Tuple, Dict

from simulator import *
from load_data import load_md_from_file
from my_strategy import MyStrategy
from get_info import get_metrics, md_to_dataframe

In [3]:
MARKET_DATA_PATH = '../md/btcusdt:Binance:LinearPerpetual/'

# Model
Using arithmetic Brownian motion with drift

**1. Reservation price**
$$ r(s, t) = s + b(T − t) −q(2η+γσ^2(T −t)).$$

- $s$ is mid-price.
- $q$ is position size in base asset.
- $T$ is terminal time.
- $t$ is current time.
- $\sigma$ is volatiliaty of standard Brownian motion.
- $b$ drift coefficient.
- $\gamma$ is risk aversity.
- $η \ge 0$ -- penalty.

$\sigma$, $\gamma$, $b$ and $η$ are parameters of the strategy.

**2. Spread**

$$ \delta^a + \delta^b = \frac{2}{\gamma} \log\left(1 + \frac{\gamma}{k}\right) + 2η + \gamma\sigma^2(T-t).$$

Here $k = \alpha K$, where
- $\alpha$ is from $f^Q(x) \propto x^{-1-\alpha}$ -- density of market order size;
- $K$ is from $\Delta p \propto K^{-1} \log(Q)$.

# Backtesting functions

In [4]:
def my_round(x, ndigits):
    return round(float(x), ndigits)

def get_metrics_numeric(metrics):
    metrics_numeric = {
        'Final PnL':    my_round(metrics['total'].iloc[-1], 2),
        'Final volume': my_round(metrics['BTC'].iloc[-1], 3)
    }
    return metrics_numeric

def backtest(md, sim_params: dict, strat_params: dict, fee: float) -> Tuple[pd.DataFrame, Dict]:
    sim = Sim(md, **sim_params)
    strategy = MyStrategy(sim, **strat_params)
    trades_list, md_list, updates_list, all_orders = strategy.run()
    metrics = get_metrics(updates_list, fee=fee)
    metrics_numeric = get_metrics_numeric(metrics)
    return metrics, metrics_numeric

In [5]:
def plot_metrics(metrics, metrics_numeric, asset, title=''):
    fig = make_subplots(rows=4, cols=1, row_heights=[0.3, 0.3, 0.2, 0.2], shared_xaxes=True, vertical_spacing=0.005)
    fig.add_trace(go.Scatter(
        name='PnL',
        x=metrics['receive_ts'],
        y=metrics['total'],
        line=dict(color=px.colors.qualitative.Plotly[0]),
        showlegend=False
    ), row=1, col=1)

    fig.add_trace(go.Scatter(
        name='Mid-price',
        x=metrics['receive_ts'],
        y=metrics['mid_price'],
        line=dict(color=px.colors.qualitative.Plotly[5]),
        showlegend=False
    ), row=2, col=1)

    fig.add_trace(go.Scatter(
        name='Inventory (BTC)',
        x=metrics['receive_ts'],
        y=metrics['BTC'],
        line=dict(color=px.colors.qualitative.Plotly[4]),
        showlegend=False
    ), row=3, col=1)

    fig.add_trace(go.Scatter(
        name='Volume',
        x=metrics['receive_ts'],
        y=metrics['volume'],
        line=dict(color=px.colors.qualitative.Plotly[2]),
        showlegend=False
    ), row=4, col=1)

    metrics_numeric_txt = yaml.dump(metrics_numeric, default_flow_style=False, sort_keys=False).replace('\n', '<br>')
    fig.add_annotation(text=metrics_numeric_txt,
                       xref='paper', yref='paper', x=1, y=0.9,
                       align='left', font={'family': 'monospace'})

    time_str = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S')
    title += f'<br>Backtest on {asset}' \
             f'<br>Launch time: {time_str}'

    fig.update_layout(width=1000, height=1400,
                      title=title,
                      yaxis1_title='PnL (account worth in quote asset)', yaxis2_title='Mid-price',
                      yaxis3_title='Inventory (BTC)', yaxis4_title='Volume')
    fig.update_traces(xaxis='x5')
    fig.update_xaxes(showspikes=True, spikemode='across', spikedash='dot', spikethickness=2)
    fig.update_yaxes(showspikes=True, spikemode='across', spikedash='dot', spikethickness=2)
    return fig

# Run the backtesting

In [6]:
T = pd.Timedelta(200, 'm').delta
md = load_md_from_file(MARKET_DATA_PATH, T)

/var/folders/0s/9ph2yzfj66q6rkt2s8_1fl7m0000gn/T/ipykernel_60118/4223635110.py:1: FutureWarning: Timedelta.delta is deprecated and will be removed in a future version.
  T = pd.Timedelta(200, 'm').delta


In [7]:
sim_params = {
    'execution_latency': 10_000_000,
    'md_latency': 10_000_000
}
strat_params = {
    'b': 3,
    'eta': 0.0001,
    'gamma': 2,
    'k': 0.8,
    'sigma': 1,
    'terminal_time': False,
    'adjust_delay': 1_000_000,
    'order_size': 0.001,
    'min_order_size': 0.001,
    'precision': 2
}
FEE = 0.0

In [8]:
metrics, metrics_num = backtest(md, sim_params, {**strat_params, 'terminal_time': True}, fee=FEE)
plot_metrics(metrics[::60], metrics_num, asset='BTCUSDT', title='WITH terminal time')